In [0]:
!pip install requests-html

     |████████████████████████████████| 1.2MB 13.7MB/s 
     |████████████████████████████████| 81kB 27.4MB/s 
  Created wheel for parse: filename=parse-1.12.1-cp36-none-any.whl size=22342 sha256=3cf5c96ba31639c79016dc14be908d501a0356177d30b9d7386a4659b57999fa
  Stored in directory: /root/.cache/pip/wheels/16/f1/d5/72f7e2c22ab3d106bb6f7d727552b5e027b832284f4704b106
  Created wheel for fake-useragent: filename=fake_useragent-0.1.11-cp36-none-any.whl size=13485 sha256=a35c8a98edc4a046ae4b57a32a99ebbe594ed8863ad52d61dc78474b93e4b59e
  Stored in directory: /root/.cache/pip/wheels/5e/63/09/d1dc15179f175357d3f5c00cbffbac37f9e8690d80545143ff
  Created wheel for pyppeteer: filename=pyppeteer-0.0.25-cp36-none-any.whl size=78362 sha256=00105533cbd9fda7eae92f78c989f74d919c9d4278c8da1b4cc8d89f60216150
  Stored in directory: /root/.cache/pip/wheels/34/e0/5d/070e22eceecf7ecd5fa4b86bbc18c1c7d0b90e02e9b57f35eb
Successfully built parse fake-useragent pyppeteer


In [0]:
import re
import json
from requests_html import HTMLSession

session = HTMLSession()

url_query="https://www.pornhub.com/video/search?search={}&page={}"
url_video="https://www.pornhub.com/view_video.php?viewkey={}"

def parse_video_data(li_video):
  views_str = li_video.find(".thumbnail-info-wrapper .videoDetailsBlock var",first=True).text
  views = 0
  if views_str[-1] is 'K':
    views = int(float(views_str[:-1]) * 1000)
  elif views_str[-1] is 'M':
    views = int(float(views_str[:-1]) * 1000000)
  else:
    views = int(views_str)
    
  rating = int(li_video.find(".thumbnail-info-wrapper .videoDetailsBlock .rating-container .value",first=True).text[:-1])
  
  duration_parts = li_video.find(".marker-overlays .duration",first=True).text.split(':')
  duration = int(duration_parts[-1])
  duration += int(duration_parts[-2])*60
  if len(duration_parts)>2:
    duration += int(duration_parts[-3])*60*60
    
  lifespan = 0 
  added_parts = li_video.find(".thumbnail-info-wrapper .videoDetailsBlock .added",first=True).text.split(' ')
  if len(added_parts) is 1:
    lifespan = 24*60*60
  elif added_parts[1].startswith("min"):
    lifespan = int(added_parts[0]) * 60
  elif added_parts[1].startswith("hour"):
    lifespan = int(added_parts[0]) * 60 * 60
  elif added_parts[1].startswith("day"):
    lifespan = int(added_parts[0]) * 60 * 60 * 24
  elif added_parts[1].startswith("week"):
    lifespan = int(added_parts[0]) * 60 * 60 * 24 * 7
  elif added_parts[1].startswith("month"):
    lifespan = int(added_parts[0]) * 60 * 60 * 24 * 7 * 30
  elif added_parts[1].startswith("year"):
    lifespan = int(added_parts[0]) * 60 * 60 * 24 * 7 * 30 * 12
  
  user_link = li_video.find(".thumbnail-info-wrapper .videoUploaderBlock .usernameWrap a",first=True)
  username = None
  if user_link != None:
    username = user_link.text
  return {
      'id': li_video.attrs['data-id'],
      'vkey': li_video.attrs['_vkey'],
      'duration': duration,
      'isHD': li_video.find(".marker-overlays .hd-thumbnail",first=True)!=None,
      'title': li_video.find(".thumbnail-info-wrapper span.title a",first=True).text,
      'views': views,
      'raiting': rating,
      'lifepsan': lifespan,
      'user': username,
      'isVerified': li_video.find(".thumbnail-info-wrapper .videoUploaderBlock .own-video-thumbnail",first=True)!=None
  }

def get_video_meta(html_video):
  javascript = html_video.html.find("#player script",first=True).text
  id = html_video.html.find("#player",first=True).attrs['data-video-id']
  match= re.search("var flashvars_{} = ".format(id)+"(.+?);", javascript)
  if match is not None:
    return json.loads(match.group(1))
  return None

def parse_videos(session, url):
  r = session.get(url)  
  li_videos = r.html.find("#videoSearchResult .videoblock")
  return {
      'hasNext': r.html.find(".pagination3 .page_next a", first=True)!=None,
      'videos': list(map(parse_video_data, li_videos))
  }

# r_video = session.get(url_video.format(video_data['vkey']))
# video_meta = get_video_meta(r_video)
# print(video_meta)

page = 1
has_next_a = True
while has_next_a:
  print('page: {}'.format(page))
  videos_data = parse_videos(session, url_query.format("compilation",page))
  has_next_a = videos_data['hasNext']
  page+=1
  print(videos_data['videos'])
  



page: 1
[{'id': '250242071', 'vkey': 'ph5d8873b634154', 'duration': 1855, 'isHD': True, 'title': "The Only Porn Compilation You'll Ever Need (Huge HD Comp w/ NO MUSIC)", 'views': 183000, 'raiting': 82, 'lifepsan': 1814400, 'user': 'compking17', 'isVerified': False}, {'id': '246334911', 'vkey': 'ph5d70a8dfb516f', 'duration': 3782, 'isHD': True, 'title': "Pmvfiend's Ultimate Porn Compilation 2019", 'views': 138000, 'raiting': 83, 'lifepsan': 18144000, 'user': 'pmv-fiend', 'isVerified': False}, {'id': '99537232', 'vkey': 'ph5857949a84aad', 'duration': 2208, 'isHD': True, 'title': 'The Hottest Girls In Porn Huge HD Compilation (154 Girls w/ Names)', 'views': 22700000, 'raiting': 80, 'lifepsan': 435456000, 'user': None, 'isVerified': False}, {'id': '249888821', 'vkey': 'ph5d8659e35f239', 'duration': 622, 'isHD': True, 'title': 'Girls Just Wanna Have Fun! Electro PMV - Male Stripper Party Compilation', 'views': 110000, 'raiting': 81, 'lifepsan': 1814400, 'user': 'Muizzixx', 'isVerified': Fal

KeyboardInterrupt: ignored